

# RDBバックエンドを使用したスタディの保存/再開

RDBバックエンドを使用すると、スタディの永続化（保存と再開）やスタディ履歴の参照が可能になります。
さらに、この機能を利用してマルチノード環境での最適化タスクを実行できます。詳細は `distributed` を参照してください。

このセクションでは、SQLiteデータベースを使用したローカル環境での簡単な例を試してみましょう。

<div class="alert alert-info"><h4>Note</h4><p>PostgreSQLやMySQLなどの他のRDBバックエンドを使用する場合は、storage引数にDBのURLを指定します。
    URLの設定方法については、[SQLAlchemyのドキュメント](https://docs.sqlalchemy.org/en/latest/core/engines.html#database-urls)_ を参照してください。</p></div>


## 新しいスタディの作成

:func:`~optuna.study.create_study` 関数を使用して、以下のように永続化可能なスタディを作成できます。
SQLiteファイル ``example.db`` が自動的に初期化され、新しいスタディレコードが作成されます。


In [ ]:
import logging
import sys

import optuna

# 標準出力にログを表示するストリームハンドラを追加
optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study_name = "example-study"  # スタディの一意の識別子
storage_name = "sqlite:///{}.db".format(study_name)
study = optuna.create_study(study_name=study_name, storage=storage_name)

スタディを実行するには、目的関数を引数として :func:`~optuna.study.Study.optimize` メソッドを呼び出します。



In [ ]:
def objective(trial):
    x = trial.suggest_float("x", -10, 10)
    return (x - 2) ** 2

study.optimize(objective, n_trials=3)

## スタディの再開

スタディを再開するには、スタディ名 ``example-study`` とDB URL ``sqlite:///example-study.db`` を指定して
:class:`~optuna.study.Study` オブジェクトをインスタンス化します。



In [ ]:
study = optuna.create_study(study_name=study_name, storage=storage_name, load_if_exists=True)
study.optimize(objective, n_trials=3)

注意: :mod:`~optuna.samplers` と :mod:`~optuna.pruners` のインスタンス状態はストレージに保存されません。
再現性のために ``seed`` 引数を指定したサンプラーでスタディを再開する場合、``pickle`` を使用して
以下のようにサンプラーを復元する必要があります::

    import pickle

    # 後で読み込むためにサンプラーをpickleで保存
    with open("sampler.pkl", "wb") as fout:
        pickle.dump(study.sampler, fout)

    restored_sampler = pickle.load(open("sampler.pkl", "rb"))
    study = optuna.create_study(
        study_name=study_name, storage=storage_name, load_if_exists=True, sampler=restored_sampler
    )
    study.optimize(objective, n_trials=3)




## 実験履歴

このセクションでは [Pandas](https://pandas.pydata.org/)_ のインストールが必要です:

```bash
$ pip install pandas
```
:class:`~optuna.study.Study` クラスを使用してスタディとトライアルの履歴にアクセスできます。
例えば、``example-study`` の全トライアルを取得するには以下のようにします:



In [ ]:
study = optuna.create_study(study_name=study_name, storage=storage_name, load_if_exists=True)
df = study.trials_dataframe(attrs=("number", "value", "params", "state"))

メソッド :func:`~optuna.study.Study.trials_dataframe` は以下のような pandas データフレームを返します:



In [ ]:
print(df)

:class:`~optuna.study.Study` オブジェクトは :attr:`~optuna.study.Study.trials`, :attr:`~optuna.study.Study.best_value`,
:attr:`~optuna.study.Study.best_params` などのプロパティも提供します (詳細は `first` を参照)。



In [ ]:
print("Best params: ", study.best_params)
print("Best value: ", study.best_value)
print("Best Trial: ", study.best_trial)
print("Trials: ", study.trials)